In [ ]:
!pip install transformers
!pip install pytorch_lightning

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 4.4 MB 4.9 MB/s 
     |████████████████████████████████| 101 kB 14.9 MB/s 
     |████████████████████████████████| 6.6 MB 56.5 MB/s 
     |████████████████████████████████| 596 kB 72.7 MB/s 
  Attempting uninstall: pyyaml
    Found existing installation: PyYAML 3.13
    Uninstalling PyYAML-3.13:
      Successfully uninstalled PyYAML-3.13
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 585 kB 5.0 MB/s 
     |████████████████████████████████| 140 kB 50.6 MB/s 
     |████████████████████████████████| 419 kB 52.3 MB/s 
     |████████████████████████████████| 1.1 MB 66.1 MB/s 
     |████████████████████████████████| 144 kB 66.1 MB/s 
     |████████████████████████████████| 94 kB 4.6 MB/s 
     |████████████████████████████████| 271 kB 72.0 MB/s 


In [ ]:
from transformers import PreTrainedTokenizerFast
tokenizer = PreTrainedTokenizerFast.from_pretrained("skt/kogpt2-base-v2", eos_token="</s>")

import torch
from transformers import GPT2Config, GPT2LMHeadModel

device = torch.device("cpu")

pretrained_model_config = GPT2Config.from_pretrained("skt/kogpt2-base-v2")
model = GPT2LMHeadModel(pretrained_model_config).to(device)

fine_tuned_model_ckpt = torch.load("/content/drive/MyDrive/11_recipe_generator/model/epoch=3-val_loss=2.19-v1.ckpt", map_location=torch.device("cpu"))
model.load_state_dict({k.replace("model.", ""): v for k, v in fine_tuned_model_ckpt['state_dict'].items()})

model.eval()

Downloading:   0%|          | 0.00/2.69M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/0.98k [00:00<?, ?B/s]

The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'GPT2Tokenizer'. 
The class this function is called from is 'PreTrainedTokenizerFast'.


GPT2LMHeadModel(
  (transformer): GPT2Model(
    (wte): Embedding(51200, 768)
    (wpe): Embedding(1024, 768)
    (drop): Dropout(p=0.1, inplace=False)
    (h): ModuleList(
      (0): GPT2Block(
        (ln_1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (attn): GPT2Attention(
          (c_attn): Conv1D()
          (c_proj): Conv1D()
          (attn_dropout): Dropout(p=0.1, inplace=False)
          (resid_dropout): Dropout(p=0.1, inplace=False)
        )
        (ln_2): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (mlp): GPT2MLP(
          (c_fc): Conv1D()
          (c_proj): Conv1D()
          (act): NewGELUActivation()
          (dropout): Dropout(p=0.1, inplace=False)
        )
      )
      (1): GPT2Block(
        (ln_1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (attn): GPT2Attention(
          (c_attn): Conv1D()
          (c_proj): Conv1D()
          (attn_dropout): Dropout(p=0.1, inplace=False)
          (resid_dropout): Dro

In [ ]:
model.eval()

GPT2LMHeadModel(
  (transformer): GPT2Model(
    (wte): Embedding(51200, 768)
    (wpe): Embedding(1024, 768)
    (drop): Dropout(p=0.1, inplace=False)
    (h): ModuleList(
      (0): GPT2Block(
        (ln_1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (attn): GPT2Attention(
          (c_attn): Conv1D()
          (c_proj): Conv1D()
          (attn_dropout): Dropout(p=0.1, inplace=False)
          (resid_dropout): Dropout(p=0.1, inplace=False)
        )
        (ln_2): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (mlp): GPT2MLP(
          (c_fc): Conv1D()
          (c_proj): Conv1D()
          (act): NewGELUActivation()
          (dropout): Dropout(p=0.1, inplace=False)
        )
      )
      (1): GPT2Block(
        (ln_1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (attn): GPT2Attention(
          (c_attn): Conv1D()
          (c_proj): Conv1D()
          (attn_dropout): Dropout(p=0.1, inplace=False)
          (resid_dropout): Dro

In [ ]:
import pandas as pd

# 레시피 데이터프레임
testset_for_custom_metric = pd.DataFrame(columns = ['input', 'ingredients'])

lines = open("/content/drive/MyDrive/11_recipe_generator/data/test_for_custom_metric.reg.txt", "r", encoding="utf-8").readlines()

test = ''
for i,line in enumerate(lines):
  inputs = ''
  input_end = line.find('<unused3>')
  inputs = line[:input_end+9]
  
  ingredients = ''
  ingredient_start = line.find('<unused2>')
  ingredient_end = line.find('<unused3>')
  ingredients = line[ingredient_start+9:ingredient_end-1].split('$')

  testset_for_custom_metric.loc[i] = [inputs, ingredients]

In [ ]:
df = testset_for_custom_metric.copy()

In [ ]:
from tqdm import notebook
from tqdm import tqdm

evaluation_size = 10
repetition_penalties=[1,1.1,1.2,1.3,1.5,1.75,1.9]
temperatures=[0.9, 0.8, 0.7, 0.6, 0.5, 0.4, 0.3, 0.2, 0.1] # temperature 값이 0에 가까울 수록 원래 컸던 확률은 더 커지고 원래 작았던 확률은 더 작아지는 정도가 높아진다.
top_ks=[30, 40, 50] # 확률값이 가장 높은 k개 토큰들 중에 하나를 선택하는 방법
top_ps=[0.92, 0.93, 0.94] # 확률값이 높은 순서대로 내림차순 정렬을 한 뒤 누적 확률값이 p 이상인 최소 개수의 토큰들 중 하나를 선택

max_length = model.config.n_positions
stride = 256

result_df = pd.DataFrame(columns=['name','perplexity'])

for repetition_penalty in notebook.tqdm(repetition_penalties, desc='repetition_penalty'):
    for temperature in notebook.tqdm(temperatures, desc = 'temperature'):
        for top_k in notebook.tqdm(top_ks,  desc = 'top_k'):
            for top_p in notebook.tqdm(top_ps, desc = 'top_p'):
                evaluation_result = []
                nlls = []

                for k in range(0, evaluation_size):
                    instance = []
                    input_text = df['input'][k]
                    input_ids = tokenizer.encode(input_text, return_tensors='pt')
                    with torch.no_grad():
                        generated_ids = model.generate(
                            input_ids,
                            do_sample=True,
                            min_length=50,
                            max_length=250,
                            repetition_penalty=repetition_penalty,
                            no_repeat_ngram_size=2,
                            temperature=temperature,
                            top_k=top_k,
                            top_p=top_p,
                        )

                        output = tokenizer.decode([el.item() for el in generated_ids[0]])
                        preprocessed_output = output.split('<unused4>')[1].split('<unused5>')[0]
                        print(preprocessed_output)

                        # perplexity
                        temp = tokenizer(preprocessed_output, return_tensors='pt')

                        for i in range(0, temp.input_ids.size(1), stride):
                          begin_loc = max(i+stride-max_length, 0)
                          end_loc = min(i+stride, temp.input_ids.size(1))
                          trg_len = end_loc - i

                          input_ids = temp.input_ids[:, begin_loc:end_loc]
                          target_ids = input_ids.clone()
                          target_ids[:, :-trg_len] = -100

                          with torch.no_grad():
                            outputs = model(input_ids, labels=target_ids)
                            neg_log_likelihood = outputs[0] * trg_len
                            print(neg_log_likelihood)

                          nlls.append(neg_log_likelihood)

                        ppl = torch.exp(torch.stack(nlls).sum() / end_loc).numpy()

                        data_to_insert = {'name' : f"rep:{repetition_penalty}_temp:{temperature}_topk:{top_k}_topp:{top_p}", 'perplexity': ppl}
                        result_df = result_df.append(data_to_insert, ignore_index=True)

repetition_penalty:   0%|          | 0/7 [00:00<?, ?it/s]

temperature:   0%|          | 0/9 [00:00<?, ?it/s]

top_k:   0%|          | 0/3 [00:00<?, ?it/s]

top_p:   0%|          | 0/3 [00:00<?, ?it/s]

 이 맥남입니다 김치를 넣어서 김치 국물을 만들 거예요 김치랑 고추랑 같이 먹으면 아주 좋은 요리가 되겠죠 김치와 함께 볶아 먹는 소스와는 다른 메뉴예 요 자 시작합니 다 재료는 재료란을 참고해 주세요 매운 걸 싫어하시는 분들은 청양고추를 추가로 넣어주세요 삶은 계란은 준비해주세요. 오이는 반달 썰기로 썰어서 준비해 주시고 고추장 2큰 술을 넣어주면 더 맛있는데요 저는 매운 거 못 먹는 분이라 살짝 더 매운맛으로 짰어요 신 김치는 냉장고에 넣어두었어요. 저번에 만들어 둔 김치 볶은 것을 사용하셔도 되고 요렇게 해서 만들었다면 물에 한 번 헹궈 주셔서 준비하시면 더 좋아요 오이를 넣으면 아삭한 식감이 느껴지면서 씹히는 식감을 좋아하실 거 같아 요 양념장은 간장 2 큰 술 식초 1 큰  설탕 2-2 큰 술을 넣고 조물조금 추가해 주시
tensor(450.3683)
 두유와 아몬드는 잘게 다져서 아몬드 슬라이스와 함께 섞어주세요.분량의 재료를 모두 섞어 크림화한 후 냉동 보관해 주세요.*냉장 보관하여 드시려면 실온 보관하시길 추천해 드세요!
tensor(126.4830)
 템 페 간 장 식초 메이플 시럽을 넣고 섞어 소스를 만든다. 템페스 소스에 템페이 소스 소금 후추 템 페이 소스가 섞이면 소스는 완성
tensor(148.4710)
 손질한 재료를 두세 가지 재료로 만든 치대어 촉촉한 치즈케이크를 만들어 보도록 할게요. 달걀은 흰자와 노른자를 분리한 뒤 흰자를 노랗게 휘핑해 주세요. 흰자에 설탕 분말 코코넛 오일을 넣어 섞고 노름자에는 코코아 가루 코코아가루를 넣어 섞어 주세요 흰자는 머랭을 쳐 주세 요 가루 재료인 계란과 코코아, 가루, 가루류를 체 쳐 넣고 섞어 반죽해 요 반죽이 뭉쳐지지 않도록 주의해서 치대주세요. 반죽에 밀가루를 묻혀 손으로 치댄 다음 냉장고에서 30분 휴지시킵니다. 180도로 예열한 오븐에서 10분 정도 구워 주세 요양념 그릇에 담아주 세요.
tensor(363.8035)
 볼에 강력분, 통밀가루를 넣고 섞어주세요. 반죽이 뭉쳐지면 물을 

...

 김치는 송송 썰어주세요. 오이는 얇게 채를 썰고 맛술과 식초를 넣어 10분 정도 절여 주세요 중면은 찬물에 담가 매운맛을 빼주고 그릇에 담아 준비해주시고, 깨는 잘게 다져준 후 참기름과 함께 버무려 밑간을 해주셔도 좋아해 요끓인 물에 소면을 펼쳐 넣고 물이 끓어오르면, 면을 넓게 펴서 젓가락으로 저어가며 삶아 준 후, 면끼리 달라붙지 않도록 잘 섞어주면 완성이랍니다!
tensor(258.6041)
 두유와 아몬드는 잘게 다져주세요.오징어는 껍질을 벗기고 먹기 좋은 크기로 잘라 주세요볼에 소스 재료를 넣어 섞어 준비해둡니다.빵은 테두리를 자르고 밀대로 밀어 펴줍니다.180도로 예열한 기름에서 노릇하게 튀겨 줍 니다.
tensor(132.2504)
 메이플로 시판되는 소스를 준비해 주세요. 간장 식초를 넣어주세요 파와 마늘을 다져줍니다. 소금 후추로 간을 해주시고 섞어 줍니다 프라이팬에 올리브 오일을 두르고 구워준 후 한 김 올려서 볶아주면 완성
tensor(177.7954)
 두부는 으깬 후 키친타월에 올려 물기를 제거해주세요. 단호박을 잘게 다져주시고 찐 단호박도 작게 잘라 준비해 주세요반죽용 믹싱볼에 달걀을 넣고 잘 섞어 반죽을 만들어 냉장고에서 30분 이상 휴지시켜줍니다. 쌀가루를 체에 쳐서 고운체에 풀어준 뒤 반죽의 농도와 농도를 맞춰가며 치대어 줍니다-달걀이 뭉쳐지면 랩으로 싼 다음 밀폐 용기에 담아 냉동실에 넣어 보관합니다.냉동실에서 하루 정도 굳힌 후에 꺼내서 사용하셔야 해 동 안 돼 요 저는 한 번 끓여서 사용해봤는데 괜찮았어요
tensor(293.8029)
 볼에 가루 재료를 넣고 주걱으로 섞어주세요.체에 친 황 설탕, 물을 넣어 섞은 후 냉장고에서 30분간 휴지시킵니다.냉장고에 보관해두었던 반죽은 실온 상태로 사용해 주세요.160도로 예열한 오븐 팬에 반죽을 올려 10~15% 정도 익혀주면 완성이예요, 구운 빵을 곁들여 맛있게 즐겨보시면 좋아요양념으로도 활용해보셔도 좋답니다!
tensor(225.5144)
 볼에서 버터와 달걀을 넣고 핸드를믹

top_p:   0%|          | 0/3 [00:00<?, ?it/s]

 김치는 송송 썰어주세요. 오이는 얇게 채를 썰고 맛술과 식초를 넣어 10분 정도 절여 주세요 중면을 삶아 찬물에 헹군 후 먹기 좋은 크기로 잘라 준비해주시고, 삶은 달걀은 반으로 자르고 볼에 담아 지단을 부쳐 가늘게 찢어 줍니다.볼 위에 양념 재료를 넣고 섞어 소스를 만들어줍니다냉동 보관한 면과 오이채를 곁들여 완성해 주시면, 더욱 깊은 맛이 일품이에 요!
tensor(248.2323)
 두유와 아몬드는 잘게 다져주세요.오븐 팬에 유산지를 깔고 과일을 올린 후 블루베리와 산 딸기를 올려 주세요.180도로 예열한 에어프라이어에 넣고 10분간 구워주면 완성
tensor(108.6835)
 메이플로 대니얼이에요- 주말에 가족들과 함께 캠핑을 갔는데 요거 참 좋아해요. 특히나 템페스트에는 소주 한잔이 최고랍니다. 이 제껏 만들어 볼까 합니까다 재료 간 장 1큰 술 식 초 2 큰술 소금 약간 후추 조금 파슬리 가루는 한데 넣고 잘 섞어 주세요. 그리고 팬에 기름을 두르고 예열한 후 편 선선하게 구워낸 비스킷 위에 올려 줍 니다.
tensor(255.9173)
 두부는 으깨고 단 호박은 쪄서 껍질을 벗긴 후 잘게 다져주세요.손질한 단호박을 우유에 담가 30분 정도 담갔다가 체에 내려 전분기를 빼고, 쌀가루를 넣어 섞어 주세요달걀흰자와 노른자를 분리해 흰자에 설탕이 잘 섞이면 반죽 재료를 넣고 골고루 섞은 후, 냉장고에 1시간 이상 휴지시킵니다.반죽을 반으로 나눠 밀대로 밀어 편썰어 준비하고 반죽을 동그랗게 빚은 뒤 비닐봉지에 담아 10~15등분 해주시면 완성이예요,*Tip. 달걀을 풀지 않고 손으로 콕 찍어주면 터지지 않는 답니다!
tensor(272.8946)
 볼에 가루 재료를 넣고 주걱으로 섞어주세요.체에 친 황 설탕, 물을 넣어 섞은 후 냉장고에서 30분간 휴지시킵니다.냉장고에 보관해두었던 반죽은 실온 상태로 사용해주시면 돼요반죽을 둥글 납작하게 빚은 후, 따뜻한 물에 10~15% 정도 담가 주세요양념 재료와 순서 2의 반죽을 2~3등분 해주시고 오븐 팬에 올려

top_p:   0%|          | 0/3 [00:00<?, ?it/s]

 김치는 송송 썰어주세요. 오이는 얇게 채를 썰고 맛술과 식초를 넣어 10분 정도 절여 주세요 중면을 삶아 찬물에 헹군 후 먹기 좋은 크기로 잘라 준비해주시고, 삶은 달걀은 반으로 자른 뒤 볼에 담아 섞어 양념장을 만들어 버무려놔도 좋아요양념장에 고추장과 올리고당, 간장 재료를 넣고 비벼서 무쳐주면 완성이랍니다!
tensor(233.0321)
 두유와 아몬드는 잘게 다져주세요.오징어 몸통은 먹기 좋은 크기로 잘라 주세요볼에 소스 재료를 넣어 섞어 준비해주시고 블랙 올리브는 반으로 갈라 씨를 발라낸 후 블루밍 볼을 이용해 썰어 줍니다.분량의 드레싱 재료와 잘 섞고 냉장고에 차갑게 보관해 주시면 완성
tensor(168.7158)
 메이플로 시판되는 소스를 준비해 주세요. 간장 식초와 레몬즙 소금 후추 파슬리 가루는 한데 넣어 섞어주세요템 페를 구워준 후 찬물에 헹궈 물기를 빼줍니다.냄비에 간장과 식용유를 두르고 강불에서 볶아주다가 물이 끓으면 소금을 넣고 간을 맞춰 줍니다강 불 양념이 골고루 섞이면 쉐킷샤크 고기를 넣습니다. 고기가 익으면 체 친 가루를 뿌려주고 뚜껑을 덮어 약불로 30분 정도 익혀주면 완성
tensor(283.1446)
 두부는 으깨고 단 호박은 쪄서 껍질을 벗긴 후 잘게 다져주세요.손질한 재료를 볼에 넣고 섞어 주세요달걀을 풀어 지단을 부치고 찐 단호박을 넣어 잘 섞으면 완성이예요, 저는 반죽이 질어지지 않도록 주의해서 만들었답니다!완성된 요리를 그릇에 담아 맛있게 즐겨보시면 됩니다.
tensor(172.4512)
 볼에 가루 재료를 넣고 주걱으로 섞어주세요.체에 친 황 설탕, 드라이 이스트를 넣어 가볍게 섞은 후 냉장고에서 30분간 휴지시킵니다.냉장고에 보관해 주세요.160도로 예열한 오븐 팬에 반죽을 올려 170도까지 구워줍니다
tensor(157.5544)
 볼에서 가루 재료를 모두 섞어주세요. 달걀을 넣고 가볍게 섞은 후 냉장고 안에 넣어 차갑게 준비해 주세요달군 팬에 버터를 두르고 반죽을 한 국자씩 떠 올려 앞뒤로 노릇하게 구워줍니다

In [ ]:
df.to_csv("gird_search.perplexity.csv")